In [3]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

#Imports
import os
import numpy as np
import tensorflow as tf
import cv2

In [4]:
tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)


  print(pool2.shape)
  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)

In [ ]:
tf.app.run()

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_tf_random_seed': 1, '_keep_checkpoint_every_n_hours': 10000, '_save_checkpoints_steps': None, '_model_dir': '/tmp/mnist_convnet_model', '_save_summary_steps': 100}
(100, 7, 7, 64)
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-60001
INFO:tensorflow:Saving checkpoints for 60002 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:loss = 0.0782911, step = 60002
INFO:tensorflow:probabilities = [[ 0.00001183  0.00069958  0.00004526  0.00004524  0.00013473  0.00017162
   0.99880481  0.00000032  0.0000865   0.00000001]
 [ 0.00829517  0.00000016  0.00411013  0.00114362  0.

INFO:tensorflow:probabilities = [[ 0.          0.00000185  0.00005802  0.01057081  0.00000281  0.0000008
   0.00000002  0.98936194  0.00000091  0.00000286]
 [ 0.          0.00000001  0.00000004  0.9998523   0.          0.00013702
   0.          0.          0.00000058  0.00001003]
 [ 0.0001039   0.00532888  0.00045274  0.97056592  0.00000014  0.00092966
   0.          0.00546193  0.00078703  0.01636987]
 [ 0.0000509   0.0000002   0.00000804  0.00000027  0.00000133  0.00002282
   0.9998287   0.          0.00008782  0.        ]
 [ 0.00090102  0.00016936  0.92792827  0.00106583  0.00004624  0.00004156
   0.00002467  0.06957405  0.00019421  0.00005479]
 [ 0.00000004  0.00000003  0.00000021  0.00006752  0.00026924  0.00000386
   0.          0.00054156  0.0000226   0.99909496]
 [ 0.0000008   0.00002551  0.00003613  0.00139837  0.00614375  0.00302715
   0.00000092  0.00015088  0.00424872  0.98496777]
 [ 0.00001189  0.99934894  0.00000664  0.00000698  0.00001884  0.00000097
   0.00004095  0.000

INFO:tensorflow:global_step/sec: 83.077
INFO:tensorflow:loss = 0.0982832, step = 60102 (1.209 sec)
INFO:tensorflow:probabilities = [[ 0.00000028  0.00000258  0.00000001  0.00000029  0.00183762  0.00000007
   0.00000002  0.00001707  0.00000725  0.99813473]
 [ 0.98438358  0.00030149  0.00054098  0.00005001  0.00022001  0.00046725
   0.00081369  0.01151701  0.00031555  0.00139033]
 [ 0.00002048  0.00000005  0.0000016   0.00001918  0.00085186  0.00000252
   0.00000001  0.0216972   0.0000003   0.97740674]
 [ 0.00004791  0.00000006  0.00118387  0.0000745   0.00000878  0.00003328
   0.00000026  0.00009125  0.99459141  0.0039686 ]
 [ 0.00001345  0.00000833  0.00000199  0.00050804  0.00038583  0.00368453
   0.00000249  0.00233689  0.0001138   0.99294466]
 [ 0.00337341  0.00012249  0.98491096  0.00294725  0.00031854  0.0001248
   0.00036938  0.00619603  0.00020578  0.00143123]
 [ 0.7818954   0.00097414  0.18431619  0.00536702  0.00445081  0.00013152
   0.01476934  0.00025742  0.00776832  0.00006

INFO:tensorflow:probabilities = [[ 0.0009537   0.00000003  0.00001603  0.000322    0.00000043  0.00452037
   0.00044093  0.          0.99339396  0.00035256]
 [ 0.00000372  0.00000006  0.00000457  0.00001863  0.00000002  0.99833846
   0.00148877  0.          0.00014267  0.00000301]
 [ 0.00022263  0.00378891  0.00082599  0.00000065  0.0000054   0.00269335
   0.99209589  0.          0.00036724  0.00000001]
 [ 0.00000014  0.00610601  0.00010572  0.00000648  0.00000069  0.00000112
   0.          0.99334091  0.00043504  0.0000038 ]
 [ 0.00000105  0.          0.00004822  0.00000041  0.00000073  0.00000004
   0.00000007  0.000001    0.99994493  0.00000352]
 [ 0.00000002  0.00000015  0.00000006  0.00004794  0.00089778  0.00000022
   0.          0.0004054   0.00000699  0.99864143]
 [ 0.00037209  0.00045764  0.00329708  0.01265319  0.00002549  0.00025501
   0.00000461  0.00012217  0.98026478  0.00254793]
 [ 0.00000001  0.00000001  0.          0.          0.99998224  0.00000004
   0.00000011  0.00

INFO:tensorflow:global_step/sec: 79.738
INFO:tensorflow:loss = 0.0652177, step = 60202 (1.250 sec)
INFO:tensorflow:probabilities = [[ 0.00001004  0.          0.00000128  0.00908248  0.00000048  0.00264016
   0.00000003  0.00012342  0.00001931  0.98812276]
 [ 0.          0.          0.          0.          0.99999988  0.          0.
   0.          0.00000003  0.00000008]
 [ 0.00000036  0.99959534  0.00000434  0.00001027  0.0000325   0.000001
   0.00002016  0.00002948  0.00030583  0.00000069]
 [ 0.00000004  0.0000007   0.00000015  0.00094021  0.00000149  0.99878603
   0.00000615  0.          0.00016465  0.00010053]
 [ 0.00000065  0.00000326  0.00000269  0.00001718  0.00076531  0.00002381
   0.00000063  0.00001893  0.00023597  0.99893147]
 [ 0.000136    0.00000224  0.00034781  0.99734843  0.00000003  0.00014279
   0.          0.00079346  0.00050826  0.00072099]
 [ 0.00000212  0.00257296  0.00000333  0.00170721  0.00101974  0.00027012
   0.00000165  0.00275791  0.00104011  0.99062485]
 [ 0

...

INFO:tensorflow:probabilities = [[ 0.00000007  0.99986601  0.00000557  0.00000056  0.00009254  0.00000003
   0.00000087  0.00002119  0.00001237  0.00000092]
 [ 0.99981636  0.00001975  0.00001398  0.00000045  0.00000001  0.0001437
   0.00000207  0.00000087  0.00000011  0.00000277]
 [ 0.99288732  0.00002119  0.00000358  0.00000001  0.0000004   0.00000477
   0.00707557  0.00000053  0.00000008  0.00000652]
 [ 0.00000061  0.00001583  0.0003072   0.00054937  0.00000011  0.00000034
   0.          0.99834991  0.00001142  0.0007653 ]
 [ 0.0025399   0.00132458  0.00349998  0.00000668  0.000203    0.00504314
   0.00001367  0.00225586  0.98504859  0.00006461]
 [ 0.00000001  0.00000002  0.          0.00000002  0.99999344  0.00000003
   0.00000002  0.00000254  0.00000067  0.00000332]
 [ 0.00000181  0.          0.00000036  0.00000014  0.00000001  0.00003677
   0.99995947  0.          0.00000144  0.        ]
 [ 0.00009056  0.00000057  0.00036869  0.00000036  0.00173897  0.00000296
   0.00000394  0.000

INFO:tensorflow:global_step/sec: 85.4454
INFO:tensorflow:loss = 0.0101889, step = 79802 (1.173 sec)
INFO:tensorflow:probabilities = [[ 0.00000197  0.01639021  0.88308555  0.10000044  0.          0.00000016
   0.          0.00044571  0.00007586  0.00000012]
 [ 0.9850347   0.00001935  0.00062187  0.00047142  0.0000142   0.010409
   0.00321887  0.0001132   0.00008551  0.00001182]
 [ 0.00000007  0.00000278  0.00002417  0.99984896  0.00000001  0.00011487
   0.0000003   0.00000002  0.00000873  0.0000001 ]
 [ 0.00033182  0.00013512  0.00939299  0.00126292  0.95518452  0.0010735
   0.00260909  0.00093565  0.02459154  0.00448303]
 [ 0.          0.          0.          0.00000233  0.          0.99999452
   0.00000006  0.          0.00000015  0.00000293]
 [ 0.00000312  0.11336484  0.88577104  0.00074952  0.00000127  0.00000312
   0.00005662  0.0000001   0.00005033  0.00000001]
 [ 0.00000497  0.00000057  0.00039594  0.00006659  0.00000003  0.00000002
   0.          0.99952209  0.00000258  0.000007

INFO:tensorflow:probabilities = [[ 0.00000001  0.00000003  0.00000001  0.00000839  0.00000001  0.99998391
   0.          0.0000001   0.00000053  0.00000711]
 [ 0.00000007  0.00000245  0.00001738  0.99980551  0.          0.00002167
   0.          0.00000026  0.00013127  0.00002137]
 [ 0.00000316  0.00000377  0.00000997  0.00000013  0.00000055  0.00003927
   0.99990094  0.00000038  0.00004161  0.00000018]
 [ 0.00000542  0.00002812  0.00010866  0.00008519  0.00000153  0.00000047
   0.00000001  0.99794346  0.00000212  0.00182503]
 [ 0.00000011  0.          0.00000004  0.00007682  0.          0.99985373
   0.00003132  0.00000002  0.00000465  0.00003326]
 [ 0.00000001  0.00018654  0.99978346  0.0000285   0.          0.          0.
   0.00000001  0.00000158  0.        ]
 [ 0.00000043  0.00000003  0.00000002  0.          0.00000009  0.00000075
   0.99999797  0.          0.00000073  0.        ]
 [ 0.00076521  0.0000004   0.00017002  0.00002685  0.0000201   0.00079579
   0.00171106  0.00000041  

INFO:tensorflow:global_step/sec: 80.7118
INFO:tensorflow:loss = 0.0161881, step = 79902 (1.237 sec)
INFO:tensorflow:probabilities = [[ 0.00000003  0.00000001  0.          0.00000164  0.00000002  0.99999714
   0.00000007  0.          0.00000003  0.00000108]
 [ 0.00000014  0.          0.00003511  0.00000236  0.00000004  0.00000459
   0.00000064  0.          0.9998771   0.00008001]
 [ 0.00000009  0.00000001  0.00000005  0.00000077  0.00028635  0.00000072
   0.00000003  0.0000233   0.00000509  0.99968362]
 [ 0.00000002  0.00000029  0.00000091  0.00030913  0.00021072  0.00000003
   0.          0.00618271  0.00014176  0.99315453]
 [ 0.          0.00000001  0.          0.          0.99998951  0.00000001
   0.          0.00000638  0.0000003   0.00000372]
 [ 0.00001421  0.00000488  0.99417275  0.00082354  0.00000036  0.00000002
   0.00000002  0.00000741  0.00496988  0.00000704]
 [ 0.00000028  0.00006473  0.00000642  0.99988568  0.00000011  0.00002948
   0.          0.00000027  0.00001141  0.000

INFO:tensorflow:probabilities = [[ 0.99996257  0.00000001  0.00000017  0.00000031  0.00000001  0.00000241
   0.00000045  0.00002572  0.00000002  0.00000849]
 [ 0.00000049  0.00001448  0.00035444  0.00065841  0.00000021  0.00000239
   0.0000002   0.00000247  0.99895895  0.00000793]
 [ 0.00000001  0.00017087  0.00138011  0.0005627   0.00000007  0.00000005
   0.          0.99780625  0.00007722  0.0000027 ]
 [ 0.00000018  0.00000232  0.00000008  0.00095854  0.00000071  0.99894458
   0.00000039  0.00003898  0.00004526  0.00000902]
 [ 0.00000015  0.00000258  0.00000033  0.0000065   0.          0.00000013
   0.          0.9999069   0.00000115  0.00008222]
 [ 0.00000282  0.00000288  0.0000024   0.00002567  0.98943335  0.00000864
   0.00006755  0.00066349  0.00183871  0.00795443]
 [ 0.86400926  0.00018541  0.13160089  0.00249965  0.00023182  0.00000849
   0.00047769  0.0000164   0.00096582  0.00000462]
 [ 0.00000081  0.00007647  0.00001909  0.00064374  0.00030106  0.00001278
   0.00000001  0.94